In [178]:
import pandas as pd
import re
import httpx
from string import Template
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [179]:
def process_salary(salary_string):
    currency_signs = {
        "$": "USD",
        "€": "EUR",
        "£": "GBP",
        "₹": "INR",
        "¥": "JPY",
        "AED": "AED",
        "QAR": "QAR",
    }
    try:
        # currency = salary_string.split()[0]
        currency_match = re.match(r"([^\d\s]+)", salary_string)  
        currency = currency_match.group(1) if currency_match else None
        currency = currency_signs.get(currency, currency)
        
        for sign, full_name in currency_signs.items():
            if sign in salary_string:
                currency = full_name
                break
        if "-" in salary_string:
            salary_range = salary_string.split("-")
            lower = int("".join(filter(str.isdigit, salary_range[0])))
            upper = int("".join(filter(str.isdigit, salary_range[1])))
        else:
            lower = upper = int("".join(filter(str.isdigit, salary_string)))
        if "year" in salary_string.lower():
            lower /= 12
            upper /= 12
        avg = (lower + upper) / 2
        return currency, lower, upper, avg
    except Exception as e:
        print(f"Error processing salary string: {salary_string}, Error: {e}")
        return None, None, None, None

def calculate_salary_avg(salary_string):
    if not isinstance(salary_string, str):
        return None

    if "-" in salary_string:
        salary_range = salary_string.split("-")
        lower = "".join(filter(str.isdigit, salary_range[0]))
        upper = "".join(filter(str.isdigit, salary_range[1]))
        
        if lower and upper:
            avg_salary = (int(lower) + int(upper)) / 2
        else:
            return None  
    else:
        salary_digits = "".join(filter(str.isdigit, salary_string))
        if salary_digits:
            avg_salary = int(salary_digits)
        else:
            return None  
    
    return avg_salary
    
def extract_years_experience(description):
    match = re.search(r"(\d+)\s*(?:\+?\s*years?|year)", description.lower())
    return int(match.group(1)) if match else 0  

conversion_rates = {
    'QAR': 1 / 3.64,  # 1 USD = 3.64 QAR
    'AED': 1 / 3.67,  # 1 USD = 3.67 AED
    'USD': 1  # 1 USD = 1 USD
}

def convert_to_usd(row, salary_column):
    return row[salary_column] * conversion_rates[row['currency']]

title_mapping = { 
    'developer': [
        'software engineer', 'programmer', 'developer', 'front end web developer', 
        'back end developer', 'full stack developer', 'native android/mobile developer', 
        'ZOHO Developer', 'Full Stack Developer', 'Mobile App Developer - Flutter', 
        'php developer', 'Web Developer', 'Magento Developer', 'Low code - No code Developer', 
        'E-Commerce Executive', 'Production Support - .Net , Payments Systems - Bank', 
        'Business Development Executive - Female', 'Graphic Designer cum Photo and Videographer', 
        'Large Format Printer Operator/Graphic Designer', 'Graphic designer', 'cloud engineer', 
        'devops engineer', 'javascript developer', 'python developer', 'angular developer', 
        'react developer', 'ruby on rails developer', 'mobile game developer'
    ],
    'data scientist': [
        'data analyst', 'machine learning engineer', 'data scientist', 'big data engineer', 
        'data engineer', 'data visualization specialist', 'AI researcher', 'quantitative analyst', 
        'data architect'
    ],
    'marketing': [
        'marketing specialist', 'sales & marketing specialist', 'digital marketing', 
        'marketing manager', 'marketing executive', 'marketing officer', 
        'female arabic speaking marketing/social media executive - part time', 
        'marekting executive-female', 'Marketing Executive (Female Only)', 'Business Development Executive - Female', 
        'Marketing & Sales Executive', 'Marketing Coordinator', 'Pardot Digital Marketing', 
        'Marketing Account Manager-UAE LOCALS ONLY', 'Arabic Content Writer Social Media - Marketing Agency', 
        'Google Ad Marketer', 'Business Development Manager', 'E-commerce Manager', 'content strategist', 
        'brand manager', 'SEO specialist', 'PPC manager', 'social media manager', 'digital advertising specialist', 
        'brand ambassador', 'email marketing manager', 'Marketing Coordinator'
    ],
    'nurse': [
        'nurse', 'registered nurse', 'home care nurse', 'occupational therapist', 'dermatology nurse', 
        'female derma nurse', 'Registered Nurse with or without MOH License.', 
        'Registered Nurse (Tagalog speaking Female)for home care', 'MOH NURSE REQUIRED FOR A MEDICAL CENTER IN AJMAN', 
        'General Practitioner - Male - MOH', 'MOH Registered Nurse', 'Nursing Assistant', 'Home care nurse', 
        'Registered Nurse(female malayalam speaking) with DOH FOR HOME CARE', 'DHA Field Nurse', 
        'Home Care Massage Therapist/Home Nurse', 'DHA Beauty Therapist/GP', 'Staff Nurse', 
        'REGISTERED NURSE - DERMATOLOGY & LASER CLINIC AL WASL ROAD (PNOY- DHF)', 'DHA REGISTERED NURSE-DERMA', 
        'NURSE WITH IELTS', 'pediatric nurse', 'mental health nurse', 'ICU nurse', 'emergency room nurse', 
        'surgical nurse', 'nurse practitioner', 'midwife'
    ],
    'sales': [
        'sales manager', 'sales executive', 'sales representative', 'sales consultant', 'sales assistant', 
        'outdoor sales executive', 'sales team', 'sales girl', 'sales account executive', 'sales agent', 
        'indoor and outdoor sale executive', 'sales executive (horeca) female only', 'sales coordinator (female)', 
        'Sales Manager / Sales Consultant - Property Developer', 'Sales Executive (Outdoor)', 'Sales Coordinator', 
        'Sales Support Officer', 'Sales Excutive', 'Sales Executive (FMCG) -female only', 'Female Sales Consultant', 
        'Female Phillipino Sales', 'Female Barista', 'Sales Administrator', 'Boutique Sales Executive (Female Arabic Speakers)', 
        'Van Salesman مندوب مبيعات فان', 'Sales Executive (FMCG) -female only', 'Sales Officer (Credit Cards)', 
        'Sales Executive - Field', 'Sales Person for Building Material', 'Sales Executive - Equipment Rental & Servicing', 
        'Sale Executive', 'Sales Promotor', 'Need Female Sales Executive for Car Showroom in Dubai', 
        'Professional Sales Executive in Retail Banking', 'Retail Sales Executive', 'Sales Executive for commercial kitchen', 
        'Sales Representative (Credit Cards/Personal Loan)', 'Sales Executive-Technology Eng graduate for Event media products', 
        'Tele Sales Executive - Female', 'Sales Executive (Chinese)', 'Walkin Interviews - Sales Officers - Banking Credit Card', 
        'Outdoor Sales Lady', 'Female Phillipino Sales', 'Sales Excutive', 'regional sales manager', 'territory sales manager', 
        'inside sales representative', 'sales engineer', 'business development officer', 'account manager', 
        'relationship manager', 'Sales Cordinator'
    ],
    'finance': [
        'finance manager', 'finance executive', 'accountant', 'finance controller', 'accountant', 'senior accountant', 
        'junior accountant', 'female quickbooks accountant', 'Junior Accountant/ Cashier', 'Accountant Cum Administrator', 
        'Accountant Manufacturing Industries Experience', 'Inventory Accountant', 'Accounts Executive', 
        'Accountant cum Secretary', 'Finance Manager', 'Claims Auditor - Dentist - Insurance- TPA', 'Finance Officer', 
        'financial analyst', 'investment banker', 'tax advisor', 'financial planner', 'risk management officer', 
        'financial consultant', 'chief financial officer', 'bookkeeper'
    ],
    'customer service': [
        'customer service representative', 'telesales executive', 'call center agent', 'receptionist', 
        'office secretary', 'indoor sales & customer support representative (female only)', 
        'Customer Service - Arabic Speaking - Own Visa and Insurance', 'Female Cashier Cum Customer Service', 
        'Receptionist cum Secretary', 'Tele sales/ Customer Support Representative', 'B2C Customer Service', 'Customer Service', 
        'Customer Service Executive', 'Telecaller- Sales', 'Telesales Agaent', 'Female Cashier Cum Customer Service', 
        'Customer Support Manager', 'customer service supervisor', 'help desk support', 'client relations manager', 
        'customer experience specialist', 'client support executive', 'customer success manager',
        'Accounts Assistant Cum Data Entry', 'Customer Service - Arabic Speaking - Own Visa and Insurance',
        'Reservation Agent', 'Customer Support Executive'
    ],
    'IT': [
        'IT sales executive', 'digital print operator', 'network engineer', 'system administrator', 'IT sales executive', 
        'information technology (IT faculty/trainer/professor)', 'IT Support Executive', 'IT Executive', 'IT System Administrator', 
        'IT Professional', 'IT Service & Social Media Coordinator', 'Sap Hana BI Developer', 'ICT Sales Consultant/Account Manager', 
        'Application Developer- Oracle', 'IT Developer', 'IT Executive', 'IT Support Executive', 'cloud solutions architect', 
        'cybersecurity analyst', 'database administrator', 'IT consultant', 'data center technician', 'systems engineer', 
        'IT project manager', 'business intelligence analyst', 'IT Help Desk Support'
    ],
    'teacher': [
        'teacher', 'art teacher', 'dance teacher', 'social studies teacher', 'english tutor', 'PE teacher', 
        'arabic language teacher', 'civil engineering (faculty/trainer/professor)', 'French Teacher', 'Math Teacher', 
        'Pre KG Early years Montessori Teacher', 'Early Years Teacher', 'Trainer (Communication Expert)', 
        'Training Consultant (Sales)', 'Forex Trainer', 'Assistant Professor', 
        'TEACHING ASSISTANT - NURSERY SCHOOL IN AL BATEEN AIRPORT ROAD (PNOY-MC)', 'Optometry Training Officer', 
        'Artistic Gymnastics Coach (Female)', 'Academic Advisor', 'science teacher', 'history teacher', 'geography teacher', 
        'computer science teacher', 'language teacher', 'special education teacher', 'music teacher', 'physics teacher'
    ],
    'HR': [
        'HR assistant', 'HR admin assistant', 'HR manager', 'recruiter', 'female HR executive', 'HR generalist', 
        'HR Executive – Saudi National', 'HR Executive (Payroll)', 'HR Coordinator', 'HR and Admin Assistant', 'HR Officer', 
        'HR Executive', 'Group HR Manager', 'HR Recruitment Assistant- Census', 
        'Bright Smile Medical center Hiring female HR Assistant must residing Al Ain', 'HR Admin Assistant', 'Female HR Executive', 
        'HR Officer (female only)', 'HR Executive – Saudi National', 'HR consultant', 'talent acquisition specialist', 
        'payroll specialist', 'learning and development manager', 'compensation and benefits manager', 'HR business partner', 
        'employee relations manager'
    ],
    'food and beverage': [
        'chef', 'kitchen head', 'waitress', 'barista', 'pastry chef', 'commis 1-pastry kitchen', 'experienced specialty coffee barista', 
        'Head Pastry Chef', 'Cake chef', 'Waiter/Cashier', 'Waiter', 'Pastry Chef', 'Line cook', 'Barista/Coffee Maker', 
        'Kitchen Steward', 'Waitress', 'Restaurant Manager', 'Restaurant Manager (FEMALE)', 'Cook'
    ],
     "real estate": [
        "real estate agent", "real estate broker", "real estate consultant", "leasing consultant", 
        "property consultant", "real estate agent (experienced only)", "property portfolio consultant", 
        "real estate agent with experienced", 'Russian/Chinese Real Estate Consultant/Client Manager',
        'Real Estate Administrator', 'Sales & Leasing agent', 'Real Estate Admin ( Female& experienced only)',
        'Real Estate Agent - Female Only', 'Property Consultant/Real estate Agent', 'Real Estate Consultant',
        'Property Consultant Real Estate', 'Experienced Real Estate Agent', 'Fmale listing coordinator / call center (Real Estate)',
        'Property Management Expert/Assistant Required'
    ],
    "admin": [
        "administrative assistant", "executive assistant", "office secretary", "PA to operations manager", 
        "office girl", "office administrator cum PA", "receptionist and administrative - arabic and english speaker",
        'Admin & Telesales Staff', 'Agency Agent and Administrative Officer', 'Emirati National Administrative Officer with Tadbeer work experience', 
        'Administrator', 'Secretary', 'Executive Assistant to CEO', 'Personal Assistant/Secretary/Document controller',
        'Admin cum Accounts Assistant', 'Admin Assistant', 'Receptionist / Admin Assistant', 'Coordinator',
        'Administrative Coordinator', 'Admin Assistant (Female-Tagalog Speaker)', 'Admin cum Receptionist', 
        'Emirati National Female Administrative Officer with Tadbeer work experience', 'Office Assistant - Tagalog Speaker', 
        'Receptionist Secretary -Tagalog speaking', 'Office Administrator cum PA', 'PA to Operations Manager', 'Personal Assistant', 
        'Admin Assistant Real Estate (Female Only) (Expert in English and Arabic)'
    ],
    "construction": [
        "electrician", "forklift operator", "barber", "cleaner", "painter", "supervisor", 
        "electrician supervisor", "mig and arc welder", "surveyor", "joinery supervisor (only with technical experience in carpentry)",
        'Junior Site Engineer', 'Electrical Engineer', 'Construction Engineer', 'General Laborer', 'Mechanical Engineer', 
        'Construction Safety Officer', 'Plumber'
    ]
    
}

def process_job_title(job_title):
    try:
        job_title_cleaned = job_title.lower().strip()
        position = 'normal'
        position_keywords = ["senior", "junior", "manager", "executive", "assistant", "intern", "lead", "director"]
        
        for keyword in position_keywords:
            if keyword in job_title_cleaned:
                position = keyword
                break
        for category, synonyms in title_mapping.items():
            if any(synonym in job_title_cleaned for synonym in synonyms):
                return category, position
        return job_title_cleaned, position

    except Exception as e:
        print(f"Error processing job title: {job_title}, Error: {e}")
        return None, None

In [180]:
OLLAMA_ENDPOINT = "http://localhost:11434/api/generate"
OLLAMA_CONFIG = {
    "model": "mistral:7b-instruct-v0.2-q4_K_S",
    "keep_alive": "5m",
    "stream": False,
}

PROMPT_TEMPLATE = Template(
    """Extract the following details from the job description below, Ensure each response is concise, accurate, and formatted as specified::
    - **Job Title**: Provide the specific job title mentioned.
    - **Experience**: Extract the required experience as a single number representing years. If it's less than 1 year, use "0" (without text).
    - **Expected Salary Range**: Provide the numerical salary range in "x-y" format (without currency symbols).
    - **Expected Salary Currency**: Extract one main currency from the following options: USD, EUR, GBP, INR, JPY, AED, QAR, SAR, KD, JD.
    - **Job Type**: Extract the job type (choose from: Full-time, Part-time, Contract, Freelance, Internship, Temporary).
    - **Location**: Provide the country name only.
    - **Education Level**: Extract the education level choose one(choose from: School, High School, Diplomate, College, Bachelor, Master, PhD, Other).
    - **Major**: Extract one major (choose from: Business, Health, Social sciences and history, Engineering, Biological and biomedical sciences, Psychology, Computer and information sciences, Visual and performing arts, Communication and journalism, Education).
    - **Level**: Extract the level of the role (choose from: Senior,Mid ,Normal, Junior, Manager, Executive, Assistant, Intern, Lead, Director).
    - **Job Function**: Extract one job function (choose from: Developer, Data Scientist, Marketing, Health, Sales, Finance, Customer Service, IT, Teacher, HR, Food and Beverage, Real Estate, Admin, Construction, other).
    - **Industry**: Provide the industry type choose one(Technology, Healthcare, Education, Retail, Manufacturing, other).


    Job Description: $text

    Respond in JSON format with the keys: "Job Title", "Experience", "Expected Salary Range","Expected Salary Currency", "Job Type", "Location", "Education Level", "Major", "Level", "Job Function",  "Industry".
    As 
    - "Job Title"
    - "Experience"
    - "Salary Range"
    - "Salary Currency"
    - "Job Type"
    - "Location"
    - "Education Level"
    - "Major"
    - "Level"
    - "Job Function"
    - "Industry"
    For missing fields, use the value "missing".
    """
)

def extract_job_details(description):
    print("*"*10)
    prompt = PROMPT_TEMPLATE.substitute(text=description)
    response = httpx.post(
        OLLAMA_ENDPOINT,
        json={"prompt": prompt, **OLLAMA_CONFIG},
        headers={"Content-Type": "application/json"},
        timeout=240,
    )
    if response.status_code != 200:
        print(f"Error {response.status_code}: {response.text}")
        return None

    try:
        result = response.json()["response"].strip()
        return eval(result)  
    except Exception as e:
        print("Error parsing response:", e)
        return {
            "Job Title": "missing",
            "Experience": "missing",
            "Salary Range": "missing",
            "Salary Currency": "missing",
            "Job Type": "missing",
            "Location": "missing",
            "Education Level": "missing",
            "Major": "missing",
            "Level": "missing",
            "Job Function": "missing",
            "Industry": "missing",
        }

In [181]:
path = 'data/positions_salaries.csv' 
data = pd.read_csv(path)
data.head()

job_title  \
0                                     Spa Therapist   
1  Registered Triage Nurse NHS (Relocation Package)   
2    Sales & Marketing specialist - Food & Beverage   
3                        Food Service Crew (Female)   
4                            Digital Print Operator   

                                     job_description  \
0  · High school qualification with minimum 2 yea...   
1  Triage Nurse (Registered Nurse) – Unique Oppor...   
2  ● Minimum Experience of 3 Years in F&B Devisio...   
3  LOCAL HIRE (Must be in Doha-Qatar)\nPreferably...   
4  We are hiring - Digital Print Operator\nQAR 35...   

                      salary_string  
0     QAR 4,000 - QAR 5,000 a month  
1  QAR 148,490 - QAR 178,808 a year  
2     QAR 5,000 - QAR 6,000 a month  
3                 QAR 2,500 a month  
4     QAR 3,400 - QAR 3,500 a month

In [182]:
len(data['salary_string'].value_counts())

261

In [183]:
data.shape

(1000, 3)

In [184]:
data.isna().sum()

job_title          0
job_description    0
salary_string      0
dtype: int64

In [185]:
data[['currency', 'salary_lower', 'salary_upper', 'salary_avg']] = data['salary_string'].apply(
    lambda x: pd.Series(process_salary(x))
)

data[['salary_string', 'currency', 'salary_lower', 'salary_upper', 'salary_avg']]

salary_string currency   salary_lower   salary_upper  \
0       QAR 4,000 - QAR 5,000 a month      QAR    4000.000000    5000.000000   
1    QAR 148,490 - QAR 178,808 a year      QAR   12374.166667   14900.666667   
2       QAR 5,000 - QAR 6,000 a month      QAR    5000.000000    6000.000000   
3                   QAR 2,500 a month      QAR    2500.000000    2500.000000   
4       QAR 3,400 - QAR 3,500 a month      QAR    3400.000000    3500.000000   
5       QAR 3,000 - QAR 5,000 a month      QAR    3000.000000    5000.000000   
6                   QAR 3,000 a month      QAR    3000.000000    3000.000000   
7       AED10,000 - AED15,000 a month      AED   10000.000000   15000.000000   
8                    AED2,200 a month      AED    2200.000000    2200.000000   
9        AED8,000 - AED10,000 a month      AED    8000.000000   10000.000000   
10        AED3,000 - AED3,001 a month      AED    3000.000000    3001.000000   
11      AED40,000 - AED45,000 a month      AED   40000.000000   45000.000000   
12      AED12,000 - AED16,000 a month      AED   12000.000000   16000.000000   
13        AED6,000 - AED8,000 a month      AED    6000.000000    8000.000000   
14                   AED2,500 a month      AED    2500.000000    2500.000000   
15        AED2,000 - AED2,500 a month      AED    2000.000000    2500.000000   
16        AED2,000 - AED3,000 a month      AED    2000.000000    3000.000000   
17                   AED2,500 a month      AED    2500.000000    2500.000000   
18                   AED6,000 a month      AED    6000.000000    6000.000000   
19        AED3,000 - AED6,000 a month      AED    3000.000000    6000.000000   
20        AED5,000 - AED8,000 a month      AED    5000.000000    8000.000000   
21        AED4,500 - AED5,000 a month      AED    4500.000000    5000.000000   
22        AED2,000 - AED2,500 a month      AED    2000.000000    2500.000000   
23        AED4,000 - AED7,000 a month      AED    4000.000000    7000.000000   
24                   AED6,000 a month      AED    6000.000000    6000.000000   
25        AED3,000 - AED4,000 a month      AED    3000.000000    4000.000000   
26       AED8,000 - AED12,000 a month      AED    8000.000000   12000.000000   
27                   AED1,500 a month      AED    1500.000000    1500.000000   
28         AED2,000 - AED4,000 a week      AED    2000.000000    4000.000000   
29                  AED12,000 a month      AED   12000.000000   12000.000000   
30        AED2,000 - AED3,000 a month      AED    2000.000000    3000.000000   
31        AED3,000 - AED4,500 a month      AED    3000.000000    4500.000000   
32        AED3,000 - AED3,500 a month      AED    3000.000000    3500.000000   
33        AED3,000 - AED5,000 a month      AED    3000.000000    5000.000000   
34        AED1,600 - AED1,900 a month      AED    1600.000000    1900.000000   
35       AED7,000 - AED15,000 a month      AED    7000.000000   15000.000000   
36        AED4,000 - AED6,000 a month      AED    4000.000000    6000.000000   
37        AED4,000 - AED5,000 a month      AED    4000.000000    5000.000000   
38        AED5,000 - AED8,000 a month      AED    5000.000000    8000.000000   
39      AED10,000 - AED12,000 a month      AED   10000.000000   12000.000000   
40                   AED6,000 a month      AED    6000.000000    6000.000000   
41       AED5,000 - AED15,000 a month      AED    5000.000000   15000.000000   
42                   AED6,000 a month      AED    6000.000000    6000.000000   
43                   AED2,000 a month      AED    2000.000000    2000.000000   
44        AED3,000 - AED4,000 a month      AED    3000.000000    4000.000000   
45       AED6,000 - AED10,000 a month      AED    6000.000000   10000.000000   
46        AED5,000 - AED7,000 a month      AED    5000.000000    7000.000000   
47                   AED3,000 a month      AED    3000.000000    3000.000000   
48        AED2,500 - AED4,000 a month      AED    2500.000000    4000.000000   
49        AED3,000 - AED

In [186]:
data.isna().sum()

job_title          0
job_description    0
salary_string      0
currency           0
salary_lower       0
salary_upper       0
salary_avg         0
dtype: int64

In [187]:
data['currency'].unique()

array(['QAR', 'AED', 'USD'], dtype=object)

In [188]:
data['salary_string'].unique()

array(['QAR 4,000 - QAR 5,000 a month',
       'QAR 148,490 - QAR 178,808 a year',
       'QAR 5,000 - QAR 6,000 a month', 'QAR 2,500 a month',
       'QAR 3,400 - QAR 3,500 a month', 'QAR 3,000 - QAR 5,000 a month',
       'QAR 3,000 a month', 'AED10,000 - AED15,000 a month',
       'AED2,200 a month', 'AED8,000 - AED10,000 a month',
       'AED3,000 - AED3,001 a month', 'AED40,000 - AED45,000 a month',
       'AED12,000 - AED16,000 a month', 'AED6,000 - AED8,000 a month',
       'AED2,500 a month', 'AED2,000 - AED2,500 a month',
       'AED2,000 - AED3,000 a month', 'AED6,000 a month',
       'AED3,000 - AED6,000 a month', 'AED5,000 - AED8,000 a month',
       'AED4,500 - AED5,000 a month', 'AED4,000 - AED7,000 a month',
       'AED3,000 - AED4,000 a month', 'AED8,000 - AED12,000 a month',
       'AED1,500 a month', 'AED2,000 - AED4,000 a week',
       'AED12,000 a month', 'AED3,000 - AED4,500 a month',
       'AED3,000 - AED3,500 a month', 'AED3,000 - AED5,000 a month',
       'AED1

In [189]:
data['job_title'].unique()

array(['Spa Therapist',
       'Registered Triage Nurse NHS (Relocation Package)',
       'Sales & Marketing specialist - Food & Beverage',
       'Food Service Crew (Female)', 'Digital Print Operator',
       'Digital Marketing', 'Cashier (PhilippinesMale)',
       'Project Planner', 'Female security Guard',
       'Collections Executive', 'Receptionist', 'Finance Controller',
       'Collections Team Leader',
       'Social Media Content Creator/ PR- FEMALE', 'Office Secretary',
       'Cashier', 'UAE Bike Riders', 'Billing Clerk',
       'freelance social media and content creator',
       'PA to Operations Manager', 'Executive Assistant',
       'Logistics Customer Service Executive', 'Telesales Executive',
       'Business Setup Consultant', 'Real Estate Agent',
       'E-Commerce Executive', 'Manager - Business Setup',
       'Digital Marketing Expert Required For Marketing Educational Services',
       'Arabic video presenter', 'Optometry Training Officer',
       'Marketing Off

In [190]:
data.head()

job_title  \
0                                     Spa Therapist   
1  Registered Triage Nurse NHS (Relocation Package)   
2    Sales & Marketing specialist - Food & Beverage   
3                        Food Service Crew (Female)   
4                            Digital Print Operator   

                                     job_description  \
0  · High school qualification with minimum 2 yea...   
1  Triage Nurse (Registered Nurse) – Unique Oppor...   
2  ● Minimum Experience of 3 Years in F&B Devisio...   
3  LOCAL HIRE (Must be in Doha-Qatar)\nPreferably...   
4  We are hiring - Digital Print Operator\nQAR 35...   

                      salary_string currency  salary_lower  salary_upper  \
0     QAR 4,000 - QAR 5,000 a month      QAR   4000.000000   5000.000000   
1  QAR 148,490 - QAR 178,808 a year      QAR  12374.166667  14900.666667   
2     QAR 5,000 - QAR 6,000 a month      QAR   5000.000000   6000.000000   
3                 QAR 2,500 a month      QAR   2500.000000   2500.000000   
4     QAR 3,400 - QAR 3,500 a month      QAR   3400.000000   3500.000000   

     salary_avg  
0   4500.000000  
1  13637.416667  
2   5500.000000  
3   2500.000000  
4   3450.000000

In [191]:
len(data['job_title'].unique())

790

In [192]:
data['category'], data['position'] = zip(*data['job_title'].apply(process_job_title))
data[['job_title', 'category', 'position']]

job_title  \
0                                        Spa Therapist   
1     Registered Triage Nurse NHS (Relocation Package)   
2       Sales & Marketing specialist - Food & Beverage   
3                           Food Service Crew (Female)   
4                               Digital Print Operator   
5                                    Digital Marketing   
6                            Cashier (PhilippinesMale)   
7                                      Project Planner   
8                                Female security Guard   
9                                Collections Executive   
10                                        Receptionist   
11                                  Finance Controller   
12                             Collections Team Leader   
13            Social Media Content Creator/ PR- FEMALE   
14                                    Office Secretary   
15                                             Cashier   
16                                     UAE Bike Riders   
17                                       Billing Clerk   
18          freelance social media and content creator   
19                            PA to Operations Manager   
20                                 Executive Assistant   
21                Logistics Customer Service Executive   
22                                 Telesales Executive   
23                           Business Setup Consultant   
24                                   Real Estate Agent   
25                                E-Commerce Executive   
26                            Manager - Business Setup   
27   Digital Marketing Expert Required For Marketin...   
28                              Arabic video presenter   
29                          Optometry Training Officer   
30                                E-Commerce Executive   
31                       Marketing Officer ( in-house)   
32                       Videographer and Social Media   
33                                    Workshop Manager   
34                      Reception Guest Services Agent   
35                           Sales & Marketing Manager   
36                                      Cost Estimator   
37   Accountant (Arabic speaker only ) TADBEER EXPE...   
38                           HSE Officer with own visa   
39                                       House Manager   
40                                     Sales Executive   
41                             Real Estate Sales Agent   
42                                     Sales Executive   
43                                      Finance Intern   
44                                   Telecaller- Sales   
45                                   Marketing Manager   
46                 Digital Marketing (UAE NATIONALITY)   
47                                  Real Estate Broker   
48                           Digital Marketing Manager   
49                                       Sales Manager   
50              Administrative Assistant/Jr Accountant   
51                    BUSINESS GROWTH MANAGER - LADIES   
52                             Front End Web Developer   
53                                      Security Guard   
54                                         Electrician   
55                                 Marketing Executive   
56                            IT Sales Executive girls   
57                Team Leader - Sales (Arabic Speaker)   
58                                   Finance Executive   
59                                   Forklift Operator   
60                                     Registred nurse   
61                                  Google Ad Marketer   
62                   Wood CNC router machine operator:   
63                                     Sales Executive   
64                               Supermarket Purchaser   
65                           Telecaller - ( Abudhabi )   
66                                 FABRICATION TRAINER   
67                                             Barista   
68                                        H

In [193]:
data['category'], data['position'] = zip(*data['job_title'].apply(process_job_title))
data[['job_title', 'category', 'position']]

job_title  \
0                                        Spa Therapist   
1     Registered Triage Nurse NHS (Relocation Package)   
2       Sales & Marketing specialist - Food & Beverage   
3                           Food Service Crew (Female)   
4                               Digital Print Operator   
5                                    Digital Marketing   
6                            Cashier (PhilippinesMale)   
7                                      Project Planner   
8                                Female security Guard   
9                                Collections Executive   
10                                        Receptionist   
11                                  Finance Controller   
12                             Collections Team Leader   
13            Social Media Content Creator/ PR- FEMALE   
14                                    Office Secretary   
15                                             Cashier   
16                                     UAE Bike Riders   
17                                       Billing Clerk   
18          freelance social media and content creator   
19                            PA to Operations Manager   
20                                 Executive Assistant   
21                Logistics Customer Service Executive   
22                                 Telesales Executive   
23                           Business Setup Consultant   
24                                   Real Estate Agent   
25                                E-Commerce Executive   
26                            Manager - Business Setup   
27   Digital Marketing Expert Required For Marketin...   
28                              Arabic video presenter   
29                          Optometry Training Officer   
30                                E-Commerce Executive   
31                       Marketing Officer ( in-house)   
32                       Videographer and Social Media   
33                                    Workshop Manager   
34                      Reception Guest Services Agent   
35                           Sales & Marketing Manager   
36                                      Cost Estimator   
37   Accountant (Arabic speaker only ) TADBEER EXPE...   
38                           HSE Officer with own visa   
39                                       House Manager   
40                                     Sales Executive   
41                             Real Estate Sales Agent   
42                                     Sales Executive   
43                                      Finance Intern   
44                                   Telecaller- Sales   
45                                   Marketing Manager   
46                 Digital Marketing (UAE NATIONALITY)   
47                                  Real Estate Broker   
48                           Digital Marketing Manager   
49                                       Sales Manager   
50              Administrative Assistant/Jr Accountant   
51                    BUSINESS GROWTH MANAGER - LADIES   
52                             Front End Web Developer   
53                                      Security Guard   
54                                         Electrician   
55                                 Marketing Executive   
56                            IT Sales Executive girls   
57                Team Leader - Sales (Arabic Speaker)   
58                                   Finance Executive   
59                                   Forklift Operator   
60                                     Registred nurse   
61                                  Google Ad Marketer   
62                   Wood CNC router machine operator:   
63                                     Sales Executive   
64                               Supermarket Purchaser   
65                           Telecaller - ( Abudhabi )   
66                                 FABRICATION TRAINER   
67                                             Barista   
68                                        H

In [194]:
data['category'].value_counts()

category
sales                                                                          124
construction                                                                    71
nurse                                                                           50
finance                                                                         42
food and beverage                                                               37
marketing                                                                       28
customer service                                                                27
real estate                                                                     26
developer                                                                       22
teacher                                                                         15
admin                                                                            9
security guard                                                                

In [195]:
len(data['category'].value_counts())

484

In [196]:
data['job_title'][data['category']=='other'].unique()

array([], dtype=object)

In [197]:
path = 'data/job_descriptions_modified.csv' 
df = pd.read_csv(path)
df.head()

job_title  \
0                                     Spa Therapist   
1  Registered Triage Nurse NHS (Relocation Package)   
2    Sales & Marketing specialist - Food & Beverage   
3                        Food Service Crew (Female)   
4                            Digital Print Operator   

                                     job_description  \
0  · High school qualification with minimum 2 yea...   
1  Triage Nurse (Registered Nurse) – Unique Oppor...   
2  ● Minimum Experience of 3 Years in F&B Devisio...   
3  LOCAL HIRE (Must be in Doha-Qatar)\nPreferably...   
4  We are hiring - Digital Print Operator\nQAR 35...   

                      salary_string currency  salary_lower  salary_upper  \
0     QAR 4,000 - QAR 5,000 a month      QAR   4000.000000   5000.000000   
1  QAR 148,490 - QAR 178,808 a year      QAR  12374.166667  14900.666667   
2     QAR 5,000 - QAR 6,000 a month      QAR   5000.000000   6000.000000   
3                 QAR 2,500 a month      QAR   2500.000000   2500.000000   
4     QAR 3,400 - QAR 3,500 a month      QAR   3400.000000   3500.000000   

     salary_avg Predicted Category Predicted Level  
0   4500.000000                 IT       assistant  
1  13637.416667              nurse          senior  
2   5500.000000  food and beverage          senior  
3   2500.000000  food and beverage       assistant  
4   3450.000000                 IT       assistant

In [198]:
first_slot = df[:10]
first_slot

job_title  \
0                                     Spa Therapist   
1  Registered Triage Nurse NHS (Relocation Package)   
2    Sales & Marketing specialist - Food & Beverage   
3                        Food Service Crew (Female)   
4                            Digital Print Operator   
5                                 Digital Marketing   
6                         Cashier (PhilippinesMale)   
7                                   Project Planner   
8                             Female security Guard   
9                             Collections Executive   

                                     job_description  \
0  · High school qualification with minimum 2 yea...   
1  Triage Nurse (Registered Nurse) – Unique Oppor...   
2  ● Minimum Experience of 3 Years in F&B Devisio...   
3  LOCAL HIRE (Must be in Doha-Qatar)\nPreferably...   
4  We are hiring - Digital Print Operator\nQAR 35...   
5  We are looking for a creative, analytical and ...   
6  We are looking for an efficient, courteous cas...   
7  Who we are\nesadore International Investments ...   
8  Responsible of controlling, monitoring and aut...   
9  Our client are a multi-award winning luxury re...   

                      salary_string currency  salary_lower  salary_upper  \
0     QAR 4,000 - QAR 5,000 a month      QAR   4000.000000   5000.000000   
1  QAR 148,490 - QAR 178,808 a year      QAR  12374.166667  14900.666667   
2     QAR 5,000 - QAR 6,000 a month      QAR   5000.000000   6000.000000   
3                 QAR 2,500 a month      QAR   2500.000000   2500.000000   
4     QAR 3,400 - QAR 3,500 a month      QAR   3400.000000   3500.000000   
5     QAR 3,000 - QAR 5,000 a month      QAR   3000.000000   5000.000000   
6                 QAR 3,000 a month      QAR   3000.000000   3000.000000   
7     AED10,000 - AED15,000 a month      AED  10000.000000  15000.000000   
8                  AED2,200 a month      AED   2200.000000   2200.000000   
9      AED8,000 - AED10,000 a month      AED   8000.000000  10000.000000   

     salary_avg Predicted Category Predicted Level  
0   4500.000000                 IT       assistant  
1  13637.416667              nurse          senior  
2   5500.000000  food and beverage          senior  
3   2500.000000  food and beverage       assistant  
4   3450.000000                 IT       assistant  
5   4000.000000          marketing            lead  
6   3000.000000            finance          junior  
7  12500.000000          developer            lead  
8   2200.000000                 IT            lead  
9   9000.000000              admin       executive

In [199]:
# extracted_info = df["job_description"].apply(extract_job_details)
# print("*"*10, "Done !","*"*10) 
# extracted_df = pd.DataFrame(list(extracted_info))
# df = pd.concat([df, extracted_df], axis=1)
# df
"""-- This will may take more than 15 hours run the new saved dataset instead: """

'-- This will may take more than 15 hours run the new saved dataset instead: '

In [200]:
new_df=pd.read_csv('data/job_descriptions_with_extracted_columns1.csv')
new_df

job_title  \
0                                        Spa Therapist   
1     Registered Triage Nurse NHS (Relocation Package)   
2       Sales & Marketing specialist - Food & Beverage   
3                           Food Service Crew (Female)   
4                               Digital Print Operator   
5                                    Digital Marketing   
6                            Cashier (PhilippinesMale)   
7                                      Project Planner   
8                                Female security Guard   
9                                Collections Executive   
10                                        Receptionist   
11                                  Finance Controller   
12                             Collections Team Leader   
13            Social Media Content Creator/ PR- FEMALE   
14                                    Office Secretary   
15                                             Cashier   
16                                     UAE Bike Riders   
17                                       Billing Clerk   
18          freelance social media and content creator   
19                            PA to Operations Manager   
20                                 Executive Assistant   
21                Logistics Customer Service Executive   
22                                 Telesales Executive   
23                           Business Setup Consultant   
24                                   Real Estate Agent   
25                                E-Commerce Executive   
26                            Manager - Business Setup   
27   Digital Marketing Expert Required For Marketin...   
28                              Arabic video presenter   
29                          Optometry Training Officer   
30                                E-Commerce Executive   
31                       Marketing Officer ( in-house)   
32                       Videographer and Social Media   
33                                    Workshop Manager   
34                      Reception Guest Services Agent   
35                           Sales & Marketing Manager   
36                                      Cost Estimator   
37   Accountant (Arabic speaker only ) TADBEER EXPE...   
38                           HSE Officer with own visa   
39                                       House Manager   
40                                     Sales Executive   
41                             Real Estate Sales Agent   
42                                     Sales Executive   
43                                      Finance Intern   
44                                   Telecaller- Sales   
45                                   Marketing Manager   
46                 Digital Marketing (UAE NATIONALITY)   
47                                  Real Estate Broker   
48                           Digital Marketing Manager   
49                                       Sales Manager   
50              Administrative Assistant/Jr Accountant   
51                    BUSINESS GROWTH MANAGER - LADIES   
52                             Front End Web Developer   
53                                      Security Guard   
54                                         Electrician   
55                                 Marketing Executive   
56                            IT Sales Executive girls   
57                Team Leader - Sales (Arabic Speaker)   
58                                   Finance Executive   
59                                   Forklift Operator   
60                                     Registred nurse   
61                                  Google Ad Marketer   
62                   Wood CNC router machine operator:   
63                                     Sales Executive   
64                               Supermarket Purchaser   
65                           Telecaller - ( Abudhabi )   
66                                 FABRICATION TRAINER   
67                                             Barista   
68                                        H

In [201]:
new_df["years_experience"] = new_df["job_description"].apply(extract_years_experience)
new_df

job_title  \
0                                        Spa Therapist   
1     Registered Triage Nurse NHS (Relocation Package)   
2       Sales & Marketing specialist - Food & Beverage   
3                           Food Service Crew (Female)   
4                               Digital Print Operator   
5                                    Digital Marketing   
6                            Cashier (PhilippinesMale)   
7                                      Project Planner   
8                                Female security Guard   
9                                Collections Executive   
10                                        Receptionist   
11                                  Finance Controller   
12                             Collections Team Leader   
13            Social Media Content Creator/ PR- FEMALE   
14                                    Office Secretary   
15                                             Cashier   
16                                     UAE Bike Riders   
17                                       Billing Clerk   
18          freelance social media and content creator   
19                            PA to Operations Manager   
20                                 Executive Assistant   
21                Logistics Customer Service Executive   
22                                 Telesales Executive   
23                           Business Setup Consultant   
24                                   Real Estate Agent   
25                                E-Commerce Executive   
26                            Manager - Business Setup   
27   Digital Marketing Expert Required For Marketin...   
28                              Arabic video presenter   
29                          Optometry Training Officer   
30                                E-Commerce Executive   
31                       Marketing Officer ( in-house)   
32                       Videographer and Social Media   
33                                    Workshop Manager   
34                      Reception Guest Services Agent   
35                           Sales & Marketing Manager   
36                                      Cost Estimator   
37   Accountant (Arabic speaker only ) TADBEER EXPE...   
38                           HSE Officer with own visa   
39                                       House Manager   
40                                     Sales Executive   
41                             Real Estate Sales Agent   
42                                     Sales Executive   
43                                      Finance Intern   
44                                   Telecaller- Sales   
45                                   Marketing Manager   
46                 Digital Marketing (UAE NATIONALITY)   
47                                  Real Estate Broker   
48                           Digital Marketing Manager   
49                                       Sales Manager   
50              Administrative Assistant/Jr Accountant   
51                    BUSINESS GROWTH MANAGER - LADIES   
52                             Front End Web Developer   
53                                      Security Guard   
54                                         Electrician   
55                                 Marketing Executive   
56                            IT Sales Executive girls   
57                Team Leader - Sales (Arabic Speaker)   
58                                   Finance Executive   
59                                   Forklift Operator   
60                                     Registred nurse   
61                                  Google Ad Marketer   
62                   Wood CNC router machine operator:   
63                                     Sales Executive   
64                               Supermarket Purchaser   
65                           Telecaller - ( Abudhabi )   
66                                 FABRICATION TRAINER   
67                                             Barista   
68                                        H

In [202]:
new_df['Expected Salary Range'].isna().sum()

51

In [203]:
new_df.columns

Index(['job_title', 'job_description', 'salary_string', 'currency',
       'salary_lower', 'salary_upper', 'salary_avg', 'Predicted Category',
       'Predicted Level', 'Job Title', 'Experience', 'Expected Salary Range',
       'Expected Salary Currency', 'Job Type', 'Location', 'Education Level',
       'Major', 'Level', 'Job Function', 'Industry', 'Salary Range',
       'Salary Currency', 'Experience In Years', 'years_experience'],
      dtype='object')

In [204]:
new_df.isna().sum()

job_title                     0
job_description               0
salary_string                 0
currency                      0
salary_lower                  0
salary_upper                  0
salary_avg                    0
Predicted Category            0
Predicted Level               0
Job Title                     0
Experience                    0
Expected Salary Range        51
Expected Salary Currency     36
Job Type                      0
Location                      0
Education Level               0
Major                         0
Level                         0
Job Function                  0
Industry                      0
Salary Range                949
Salary Currency             964
Experience In Years         999
years_experience              0
dtype: int64

In [205]:
len(new_df[new_df['Major'] == 'missing'])

474

In [206]:
new_df["Major"] = new_df["Major"].where(new_df["Major"] != "missing", new_df["Predicted Category"])

In [207]:
len(new_df[new_df['Major'] == 'missing'])

0

In [208]:
len(new_df[new_df['Level'] == 'missing'])

312

In [209]:
new_df["Level"] = new_df["Level"].where(new_df["Level"] != "missing", new_df["Predicted Level"])

In [210]:
len(new_df[new_df['Level'] == 'missing'])

0

In [211]:
len(new_df[new_df['Salary Currency'] == 'missing'])

36

In [212]:
new_df["Salary Currency"] = new_df["Salary Currency"].where(new_df["Salary Currency"] != "missing", new_df["currency"])

In [213]:
len(new_df[new_df['Salary Currency'] == 'missing'])

0

In [214]:
new_df.describe()

salary_lower   salary_upper     salary_avg  years_experience
count    1000.000000    1000.000000    1000.000000       1000.000000
mean     5079.549000    6499.784833    5789.666917          2.215000
std     18693.244668   20795.228430   19714.728132          3.570648
min        49.000000      60.000000      54.500000          0.000000
25%      2000.000000    3000.000000    2500.000000          0.000000
50%      3000.000000    4000.000000    3500.000000          2.000000
75%      5000.000000    6000.000000    5500.000000          3.000000
max    560000.000000  615000.000000  587500.000000         40.000000

In [215]:
len(new_df[new_df['Salary Range'] == 'missing'])

37

In [216]:
new_df['Salary Range'].isna().sum()

949

In [217]:
new_df['Expected Salary Range'] = new_df['Expected Salary Range'].apply(calculate_salary_avg)
new_df['Expected Salary Range'] = pd.to_numeric(new_df['Expected Salary Range'], errors="coerce")
median_value = new_df['Expected Salary Range'].median()
new_df['Expected Salary Avg'] = pd.to_numeric(new_df['Expected Salary Range'], errors="coerce").fillna(median_value)
new_df['Expected Salary Avg'].isna().sum()

0

In [218]:
new_df['Expected Salary Avg']

0      4.500000e+03
1      4.068900e+04
2      5.500000e+05
3      4.500000e+03
4      3.450000e+03
5      4.000000e+05
6      3.000000e+03
7      1.250000e+06
8      1.610000e+04
9      1.500000e+02
10     3.000500e+03
11     4.250000e+06
12     1.400000e+04
13     7.000000e+05
14     2.500000e+03
15     2.250000e+03
16     2.500000e+03
17     4.500000e+03
18     4.500000e+03
19     4.500000e+05
20     6.500000e+03
21     4.750000e+03
22     2.250000e+03
23     5.500000e+05
24     6.000000e+05
25     3.500000e+03
26     1.000000e+06
27     2.000000e+03
28     3.000000e+03
29     4.500000e+03
30     2.500000e+03
31     3.750000e+03
32     3.250000e+03
33     4.000000e+03
34     1.750000e+03
35     1.100000e+04
36     5.000000e+03
37     5.500000e+03
38     6.500000e+03
39     1.100000e+06
40     3.000000e+03
41     1.000000e+04
42     3.000000e+03
43     1.000000e+03
44     3.500000e+03
45     4.500000e+03
46     6.000000e+03
47     4.500000e+03
48     3.250000e+03
49     4.000000e+03


In [219]:
new_df.describe()

salary_lower   salary_upper     salary_avg  Expected Salary Range  \
count    1000.000000    1000.000000    1000.000000           8.580000e+02   
mean     5079.549000    6499.784833    5789.666917           2.915789e+08   
std     18693.244668   20795.228430   19714.728132           8.534866e+09   
min        49.000000      60.000000      54.500000           1.100000e+01   
25%      2000.000000    3000.000000    2500.000000           2.662500e+03   
50%      3000.000000    4000.000000    3500.000000           4.500000e+03   
75%      5000.000000    6000.000000    5500.000000           2.713371e+05   
max    560000.000000  615000.000000  587500.000000           2.500004e+11   

       years_experience  Expected Salary Avg  
count       1000.000000         1.000000e+03  
mean           2.215000         2.501753e+08  
std            3.570648         7.905701e+09  
min            0.000000         1.100000e+01  
25%            0.000000         2.750000e+03  
50%            2.000000         4.500000e+03  
75%            3.000000         1.375000e+05  
max           40.000000         2.500004e+11

In [220]:
new_df['Experience'].isna().sum()

0

In [221]:
len(new_df[new_df['Experience']=='missing'])

280

In [222]:
new_df["Experience"] = new_df["Experience"].str.extract('(\d+)')
new_df["Experience"] = pd.to_numeric(new_df["Experience"], errors='ignore')

/var/folders/hz/trrpkmvx0ggf7ch6thxq7yc40000gn/T/ipykernel_1080/3234613056.py:2: FutureWarning: errors='ignore' is deprecated and will raise in a future version. Use to_numeric without passing `errors` and catch exceptions explicitly instead
  new_df["Experience"] = pd.to_numeric(new_df["Experience"], errors='ignore')


In [223]:
new_df["Experience"] = new_df["Experience"].where(new_df["Experience"] != "missing", new_df["years_experience"])
len(new_df[new_df['Experience']=='missing'])

0

In [224]:
new_df["Experience"].head()

0    1.0
1    2.0
2    3.0
3    1.0
4    2.0
Name: Experience, dtype: float64

In [225]:
len(new_df[new_df['Experience']=='missing'])

0

In [226]:
new_df['Experience'].fillna(new_df['years_experience'], inplace=True)

/var/folders/hz/trrpkmvx0ggf7ch6thxq7yc40000gn/T/ipykernel_1080/2772478545.py:1: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  new_df['Experience'].fillna(new_df['years_experience'], inplace=True)


In [227]:
new_df['Experience'].isna().sum()

0

In [228]:
currency = new_df['currency'].unique()
currency

array(['QAR', 'AED', 'USD'], dtype=object)

In [229]:
new_df['Expected_Salary_in_USD'] = new_df.apply(lambda row: convert_to_usd(row, 'Expected Salary Avg'), axis=1)
new_df['Salary_in_USD'] = new_df.apply(lambda row: convert_to_usd(row, 'salary_avg'), axis=1)

In [230]:
new_df['Expected_Salary_in_USD']

0      1.236264e+03
1      1.117830e+04
2      1.510989e+05
3      1.236264e+03
4      9.478022e+02
5      1.098901e+05
6      8.241758e+02
7      3.405995e+05
8      4.386921e+03
9      4.087193e+01
10     8.175749e+02
11     1.158038e+06
12     3.814714e+03
13     1.907357e+05
14     6.811989e+02
15     6.130790e+02
16     6.811989e+02
17     1.226158e+03
18     1.226158e+03
19     1.226158e+05
20     1.771117e+03
21     1.294278e+03
22     6.130790e+02
23     1.498638e+05
24     1.634877e+05
25     9.536785e+02
26     2.724796e+05
27     5.449591e+02
28     8.174387e+02
29     1.226158e+03
30     6.811989e+02
31     1.021798e+03
32     8.855586e+02
33     1.089918e+03
34     4.768392e+02
35     2.997275e+03
36     1.362398e+03
37     1.498638e+03
38     1.771117e+03
39     2.997275e+05
40     8.174387e+02
41     2.724796e+03
42     8.174387e+02
43     2.724796e+02
44     9.536785e+02
45     1.226158e+03
46     1.634877e+03
47     1.226158e+03
48     8.855586e+02
49     1.089918e+03


In [231]:
new_df['Salary_in_USD']

0        1236.263736
1        3746.543040
2        1510.989011
3         686.813187
4         947.802198
5        1098.901099
6         824.175824
7        3405.994550
8         599.455041
9        2452.316076
10        817.574932
11      11580.381471
12       3814.713896
13       1907.356948
14        681.198910
15        613.079019
16        681.198910
17        681.198910
18       1634.877384
19       1226.158038
20       1771.117166
21       1294.277929
22        613.079019
23       1498.637602
24       1634.877384
25        953.678474
26       2724.795640
27        408.719346
28        817.438692
29       3269.754768
30        681.198910
31       1021.798365
32        885.558583
33       1089.918256
34        476.839237
35       2997.275204
36       1362.397820
37       1226.158038
38       1771.117166
39       2997.275204
40       1634.877384
41       2724.795640
42       1634.877384
43        544.959128
44        953.678474
45       2179.836512
46       1634.877384
47        817

In [232]:
new_df = new_df.drop(columns=['Salary Range', 'Salary Currency', 
'Experience In Years', 'Job Title', 'Predicted Level',
'Predicted Category', 'salary_upper',
'salary_lower','salary_upper','salary_string',
'job_description','job_title', 'years_experience'
,'Expected Salary Avg', 'salary_avg', 'currency', 'Expected Salary Currency', 'Expected Salary Range'])
new_df

Experience                                           Job Type  \
0           1.0                                          Temporary   
1           2.0                               Full-time, Permanent   
2           3.0                                Full-time, Contract   
3           1.0                                          Full-time   
4           2.0                                          Permanent   
5           2.0                                          Permanent   
6           2.0                                          Full-time   
7           3.0                                          Full-time   
8           0.0                               Full-time, Permanent   
9           2.0                                          Full-time   
10          1.0                                          Full-time   
11          0.0                                          Full-time   
12          5.0                               Full-time, Permanent   
13          0.0                                          Full-time   
14          5.0                               Full-time, Permanent   
15          1.0                               Full-time, Permanent   
16          0.0                                          Full-time   
17          0.0                                          Full-time   
18          3.0                                          Temporary   
19          3.0                                          Full-time   
20          2.0                                          Full-time   
21          5.0                                          Full-time   
22          1.0                                          Full-time   
23          2.0                                          Full-time   
24          1.0                                          Full-time   
25          2.0                               Full-time, Permanent   
26          5.0                                          Full-time   
27          0.0                      Full-time, Part-time, Fresher   
28          0.0                                          Temporary   
29          2.0                                          Full-time   
30          1.0                                          Full-time   
31          0.0                                          Full-time   
32          2.0                                          Full-time   
33          7.0                               Full-time, Permanent   
34          1.0                               Full-time, Permanent   
35          5.0                               Full-time, Permanent   
36          3.0                                          Full-time   
37          5.0                                          Full-time   
38          5.0                                          Temporary   
39          0.0                               Full-time, Permanent   
40          3.0                                          Full-time   
41          0.0                                          Full-time   
42          3.0                                          Full-time   
43          0.0                              Full-time, Internship   
44          2.0                                          Full-time   
45          5.0                                            missing   
46          0.0                                          Full-time   
47          0.0                               Full-time, Permanent   
48          1.0                                          Full-time   
49          0.0                               Full-time, Permanent   
50          0.0                                          Full-time   
51          1.0                                          Full-time   
52          3.0                                          Full-time   
53          2.0                                          Full-time   
54          4.0                                          Full-time   
55          5.0                                          Full-time   
56          0.0

In [233]:
new_df.isna().sum()

Experience                0
Job Type                  0
Location                  0
Education Level           0
Major                     0
Level                     0
Job Function              0
Industry                  0
Expected_Salary_in_USD    0
Salary_in_USD             0
dtype: int64

In [234]:
new_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000 entries, 0 to 999
Data columns (total 10 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   Experience              1000 non-null   float64
 1   Job Type                1000 non-null   object 
 2   Location                1000 non-null   object 
 3   Education Level         1000 non-null   object 
 4   Major                   1000 non-null   object 
 5   Level                   1000 non-null   object 
 6   Job Function            1000 non-null   object 
 7   Industry                1000 non-null   object 
 8   Expected_Salary_in_USD  1000 non-null   float64
 9   Salary_in_USD           1000 non-null   float64
dtypes: float64(3), object(7)
memory usage: 78.3+ KB


In [235]:
new_df['Education Level'].value_counts()

Education Level
missing                                                       627
Bachelor                                                      170
Bachelor's                                                     51
Diploma                                                        30
High School                                                    27
Missing                                                        11
College                                                         7
High school or equivalent                                       6
Bachelor's (Preferred)                                          5
Any Graduate Holder                                             4
Degree                                                          3
Certificate                                                     3
Master's                                                        3
High School or GED                                              2
Bachelor's degree                                           

In [236]:
education_map = {
    "missing": "Unknown",
    "Missing": "Unknown",
    "High School": "High School",
    "High school or equivalent": "High School",
    "High School or GED": "High School",
    "High School Diploma": "High School",
    "High School or higher": "High School",
    "High School or Equivalent": "High School",
    "High School Graduate or General Education Degree (GED)": "High School",
    "Bachelor": "Bachelor",
    "Bachelor's": "Bachelor",
    "Bachelor's degree": "Bachelor",
    "Bachelor (Preferred)": "Bachelor",
    "Bachelor's (Preferred)": "Bachelor",
    "Bachelor's or Advanced Degree": "Bachelor",
    "Bachelor or Master": "Bachelor/Master",
    "Bachelor/Master": "Bachelor/Master",
    "Bachelor (Engineering) or Master": "Bachelor/Master",
    "Bachelor (Nursing)": "Bachelor",
    "Master's": "Master",
    "Master": "Master",
    "Master’s Degree, Diploma": "Master",
    "PhD": "Doctorate",
    "Doctorate": "Doctorate",
    "Diploma": "Diploma",
    "Degree": "Diploma",
    "Degree or Diploma": "Diploma",
    "Graduate": "Diploma",
    "Nursing": "Bachelor",
    "Medical Doctor (M.D., M.B.B.S, MBBS, MD, D.O.)": "Doctorate",
    "CA/ACCA or Equivalent": "Diploma",
    "Associate's Degree": "Diploma",
    "BSc": "Bachelor",
    "College": "College",
    "College and Bachelor": "Bachelor",
    "University Graduate": "Bachelor",
    "Engineering": "Bachelor",
    "Culinary school diploma": "Diploma",
    "Chartered Accountant, Cost Accountant, semi-qualified": "Diploma",
    "Secondary Education": "High School",
    "ITI or Diploma": "Diploma",
    "Diploma or Degree": "Diploma",
    "Technical degree": "Diploma",
    "Bachelor (French) + B.Ed.": "Bachelor",
    "Bachelor's Degree/12th (HSC)": "Bachelor",
    "12th": "High School",
    "Bachelor, Master": "Bachelor/Master",
    "Middle": "Bachelor",
    "IIT Diploma": "Diploma",
    "Degree/Diploma": "Diploma"
}
new_df['Education Level'] = new_df['Education Level'].map(education_map).fillna('Unknown')
new_df['Education Level'].value_counts()

Education Level
Unknown            653
Bachelor           240
Diploma             45
High School         42
College              7
Bachelor/Master      5
Master               5
Doctorate            3
Name: count, dtype: int64

In [237]:
new_df['Job Type'].value_counts()

Job Type
Full-time                                                        643
Full-time, Permanent                                             205
Full-time, Contract                                               39
missing                                                           36
Full-time, Permanent, Contract                                    16
Permanent                                                         10
Contract                                                           9
Temporary                                                          7
Part-time                                                          6
Full-time, Internship                                              2
Part-time, Temporary                                               2
Full-time, Temporary, Contract                                     2
Full-time, Part-time, Contract                                     2
Full-time, Permanent, Fresher                                      2
Full-time, Part-time, Per

In [238]:
job_type_map = {
    'Full-time': 'Full-time',
    'Full-time, Permanent': 'Full-time',
    'Full-time, Contract': 'Full-time',
    'Full-time, Permanent, Contract': 'Full-time',
    'Permanent': 'Full-time', 
    'Contract': 'Contract',
    'Temporary': 'Temporary',
    'Part-time': 'Part-time',
    'Full-time, Internship': 'Full-time',
    'Part-time, Temporary': 'Part-time',
    'Full-time, Temporary, Contract': 'Full-time',
    'Full-time, Part-time, Contract': 'Full-time',
    'Full-time, Permanent, Fresher': 'Full-time',
    'Full-time, Part-time, Permanent': 'Full-time',
    'Full-time, Temporary': 'Full-time',
    "['Full-time', 'Contract']": 'Full-time',  
    'Contract (3 months)': 'Contract',
    "['Full-time', 'Part-time', 'Contract']": 'Full-time', 
    'Full-time, Part-time': 'Full-time',  
    'Contract, Temporary, Full-time': 'Full-time',
    'Full-time, Permanent, Contract, Fresher': 'Full-time',
    'Full-time, Permanent, Temporary': 'Full-time',
    'Full-time, Fresher': 'Full-time',
    'Full-time, Part-time, Permanent, Temporary, Contract, Fresher': 'Full-time',
    'Freelance/Part-time': 'Freelance',
    "['Full-time', 'Part-time']": 'Full-time',  
    'Part-time, Contract': 'Part-time',
    'Internship': 'Internship',
    'Full-time, Part-time, Fresher': 'Full-time',
    'Freelance': 'Freelance',
    'missing': 'Unknown', 
}
new_df['Job Type'] = new_df['Job Type'].map(job_type_map).fillna('Unknown')
new_df['Job Type'].value_counts()

Job Type
Full-time     935
Unknown        36
Contract       10
Part-time       9
Temporary       7
Freelance       2
Internship      1
Name: count, dtype: int64

In [239]:
new_df['Location'].value_counts()

Location
Dubai                                             246
UAE                                               226
United Arab Emirates                              160
Abu Dhabi                                          73
missing                                            55
UAE (Dubai)                                        48
Qatar                                              33
UAE (Sharjah)                                      18
United Arab Emirates (Dubai)                       12
UK                                                 10
Saudi Arabia                                        8
Dubai, UAE                                          7
Abu Dhabi, UAE                                      6
United Arab Emirates (Abu Dhabi)                    6
United Arab Emirates (Sharjah)                      5
UAE (Abu Dhabi)                                     4
Sharjah                                             4
Al-Ayn                                              3
UAE(Dubai)         

In [240]:
location_map = {
    'Dubai': 'UAE', 
    'UAE': 'UAE', 
    'United Arab Emirates': 'UAE', 
    'Abu Dhabi': 'UAE', 
    'UAE (Dubai)': 'UAE', 
    'UAE (Sharjah)': 'UAE', 
    'United Arab Emirates (Dubai)': 'UAE', 
    'Dubai, UAE': 'UAE', 
    'Abu Dhabi, UAE': 'UAE', 
    'United Arab Emirates (Abu Dhabi)': 'UAE', 
    'United Arab Emirates (Sharjah)': 'UAE', 
    'UAE (Abu Dhabi)': 'UAE', 
    'Sharjah': 'UAE', 
    'Al-Ayn': 'UAE', 
    'UAE(Dubai)': 'UAE', 
    'KSA': 'Saudi Arabia', 
    'UAE-Sharjah': 'UAE', 
    'Fujairah': 'UAE', 
    'Ras al-Khaimah': 'UAE', 
    'UAE (Ras al-Khaimah)': 'UAE', 
    'UAE (United Arab Emirates)': 'UAE', 
    'Doha': 'Qatar', 
    'UAE (Ajman)': 'UAE', 
    'U.A.E': 'UAE', 
    'UAE(Abu Dhabi)': 'UAE', 
    'USA': 'USA', 
    'UAE (Fujairah)': 'UAE', 
    'UAE (AJMAN)': 'UAE', 
    'UAE (Al-Ayn)': 'UAE', 
    'UAE (AbuDhabi)': 'UAE', 
    'UAE(United Arab Emirates)': 'UAE', 
    'UAE (Abu Dhabi & Dubai)': 'UAE', 
    'UAE/Ajman': 'UAE', 
    'United Arab Emirates (UAE)': 'UAE', 
    'United Arab Emirates (Al-Ain)': 'UAE', 
    'UAE (Dubai and Ajman)': 'UAE', 
    'UAE (Umm al Quwain)': 'UAE', 
    'Medina': 'Saudi Arabia', 
    'Egypt (6th of October City)': 'Egypt', 
    'UAE-Al Ain': 'UAE', 
    'China': 'China', 
    'UAE (Dubai or Abu Dhabi)': 'UAE', 
    'Missing': 'Unknown', 
    'UAE (Sharja)': 'UAE', 
    'Ethiopia': 'MENA', 
    'healthcare': 'Unknown', 
    'UAE (RAK)': 'UAE', 
    'Iran': 'Iran', 
    'Dubai (United Arab Emirates)': 'UAE', 
    'Middle East': 'MENA', 
    'Egypt': 'Egypt', 
    'Middle East and Africa': 'MENA', 
    'United Arab Emirates (Ajman)': 'UAE', 
    'Australia': 'Europe', 
    'UAE (Dubai, Abudhabi, Sharjah, Ras al Khaimah)': 'UAE', 
    'home country': 'Unknown', 
    'Sharjah, UAE': 'UAE', 
    'United Arab Emirates - Sharjah': 'UAE', 
    'UAE, Saudi Arabia': 'Saudi Arabia', 
    'Ras Al Khaimah': 'UAE', 
    'UAE (Al Ain / Abu Dhabi)': 'UAE', 
    'Umm al-Quwain (United Arab Emirates)': 'UAE', 
    'Ajman': 'UAE', 
    'Europe': 'Europe', 
    'Grenada': 'Europe', 
    'UAE (Ras Al Khaimah)': 'UAE', 
    'UAE (Alain)': 'UAE', 
    'Remote': 'Unknown', 
    'UAE (Dubai, Sharjah & Abu Dhabi)': 'UAE', 
    'UAE-Dubai': 'UAE', 
    'Iraq/ Sudan': 'Iraq/Sudan', 
    'UAE, Ajman': 'UAE', 
    'UAE(Sharjah)': 'UAE', 
    'Dubai/Abu Dhabi': 'UAE'
}
new_df['Location'] = new_df['Location'].map(location_map).fillna('Unknown')
new_df['Location'].value_counts()

Location
UAE             870
Unknown         110
Saudi Arabia      5
Europe            3
MENA              3
Qatar             2
USA               2
Egypt             2
Iraq/Sudan        1
China             1
Iran              1
Name: count, dtype: int64

In [241]:
new_df['Major'].value_counts()

Major
Business                                                                                         99
admin                                                                                            98
sales                                                                                            92
IT                                                                                               83
customer service                                                                                 49
Health                                                                                           45
Real Estate                                                                                      41
construction                                                                                     36
HR                                                                                               34
developer                                                                                     

In [242]:
category_mapping = {
    'Business': ['Business', 'admin', 'Business Administration', 'Business Administration or Human Resources', 
                 'Business, Education', 'Business, Communications, or Marketing', 'Business or Communications', 
                 'Business Administration, Commerce or related', 'HR or Business', 'HR'],
    'Sales & Marketing': ['Sales', 'Marketing', 'Marketing, Business', 'Marketing, Business, New Media or Public Relations'],
    'IT & Computer Science': ['IT', 'developer', 'Computer and information sciences', 'Computer', 
                              'Computer and information sciences or Business', 'data scientist'],
    'Healthcare & Nursing': ['Health', 'Nursing', 'Nurse', 'Health services administration, healthcare administration', 
                             'Nursing and Health', 'Pharmacy'],
    'Real Estate & Construction': ['Real Estate', 'construction', 'Construction, Civil Engineering', 'Civil Engineering', 
                                   'Architecture', 'Architecture, Engineering or related field', 'Landscape', 
                                   'Landscape Engineering (or related field)'],
    'Finance & Accounting': ['Finance', 'Accounting or Finance', 'Accounting', 'Accounting/Finance', 'Accounting and Finance', 
                             'Accounting and Financial Processes'],
    'Food & Beverage': ['Food and Beverage', 'Food and Beverage (Restaurants Management)', 'Culinary Arts', 
                        'Culinary arts, pastry-making, baking', 'Culinary Arts, Hospitality or related field', 
                        'Culinary Arts, Hospitality and Tourism', 'Culinary management', 'Hospitality and Food Service', 
                        'Hospitality', 'Hospitality or related field'],
    'Education & Teaching': ['Education', 'teacher', 'Business Administration or Human Resources'],
    'Engineering & Technology': ['Engineering', 'Mechanical or automobile engineering', 'Industrial engineering and/or related fields', 
                                 'Engineering or Business management', 'Mechanical', 'Mechanical or automobile engineering'],
    'Other': ['Communication and Journalism', 'Communication and Journalism, Marketing', 'Communication and Journalism, Visual and performing arts',
               'Communications, Marketing, Business, New Media or Public Relations', 'Visual and performing arts', 
               'Visual and performing arts (Graphics Designing) & Communication and journalism (Social Media)', 
               'Law', 'Legal Studies', 'Logistics and Supply Chain Management', 'Logistics, Cargo and Freight Forwarding', 
               'Retail', 'Tourism', 'Travel and Tourism', 'Telecom Engineering', 'Technical and Vocational', 'Language (Arabic)', 
               'Landscape', 'Safety and Health', 'Physical Education', 'Physical Education and Coaching', 'Other', 
               'Other (Translation)', 'Fashion', 'Mechanical', 'Business, Communications, or Marketing']
}
def map_category(category):
    for key, values in category_mapping.items():
        if category in values:
            return key
    return 'Other' 

new_df['Major'] = new_df['Major'].apply(map_category)
new_df['Major'].value_counts()

Major
Other                         333
Business                      242
IT & Computer Science         144
Real Estate & Construction     84
Healthcare & Nursing           61
Sales & Marketing              45
Food & Beverage                40
Education & Teaching           20
Engineering & Technology       16
Finance & Accounting           15
Name: count, dtype: int64

In [243]:
new_df['Level'].value_counts()

Level
Normal                                                                                            386
senior                                                                                             82
executive                                                                                          82
Manager                                                                                            79
assistant                                                                                          69
Junior                                                                                             57
lead                                                                                               40
Executive                                                                                          29
Assistant                                                                                          20
manager                                                                     

In [244]:
level_mapping = {
    'Entry level': 'Junior',
    'Junior': 'Junior',
    'junior': 'Junior',
    'Mid': 'Mid',
    'mid': 'Mid',
    'Intermediate': 'Mid',
    'Senior': 'Senior',
    'senior': 'Senior',
    'Senior Role': 'Senior',
    'lead': 'Lead',
    'Lead': 'Lead',
    'Supervisor': 'Lead',
    'Manager': 'Manager',
    'manager': 'Manager',
    'Manager/Executive': 'Manager',
    'Executive': 'Executive',
    'executive': 'Executive',
    'Executive, Assistant (Preferred for marketing executive)': 'Manager',
    'Manager / Executive': 'Manager',
    'Assistant': 'Assistant',
    'assistant': 'Assistant',
    'Sales Executive': 'Manager',
    'Sales': 'Junior',
    'Sales Agent': 'Junior',
    'Agent': 'Junior',
    'Consultant': 'Senior',
    'Professional': 'Senior',
    'Coordinator': 'Senior',
    'Technician': 'Senior',
    'Technician, Engineer': 'Senior',
    'Trainer': 'Trainer',
    'Trainer/Instructor': 'Trainer',
    'Head': 'Manager',
    'Postdoctoral Fellow, Assistant Professor, Associate Professor, Full Professor, Chair Professor': 'Academic',
    'Volunteer': 'Volunteer',
    'Team Leader': 'Manager',
    'intern': 'Intern',
    'Intern': 'Intern',
    'Entry level': 'Junior',
    'Doctor': 'Senior',
    'Supporting': 'Support',
    'Welder': 'Senior',
    'Project Lead/Manager': 'Manager',
    'Foreman': 'Manager',
    'Executor': 'Manager',
    'Experienced': 'Senior',
    'Advisor': 'Senior',
    'Coach': 'Trainer',
    'General Practitioner': 'Junior',
    'Chef': 'Senior',
    'Nurse': 'Junior',
    'Missing': 'Unknown',
    'Chef': 'Senior'
}

def map_level(level):
    return level_mapping.get(level, 'Unknown')

new_df['Level'] = new_df['Level'].apply(map_level)
new_df['Level'].value_counts()

Level
Unknown      422
Executive    111
Manager      108
Senior       104
Assistant     89
Junior        85
Lead          57
Mid           14
Intern         4
Trainer        3
Academic       1
Volunteer      1
Support        1
Name: count, dtype: int64

In [245]:
new_df['Job Function'].nunique() / len(new_df) *100 

29.9

In [246]:
new_df['Job Function'].value_counts()

Job Function
Sales                                                                                                                               178
Admin                                                                                                                                57
missing                                                                                                                              51
Construction                                                                                                                         42
Food and Beverage                                                                                                                    34
Marketing                                                                                                                            33
Health                                                                                                                               31
Customer Service                   

In [247]:
new_df['Industry'].value_counts()

Industry
other                                                                                      135
Retail                                                                                     103
Healthcare                                                                                  86
Real Estate                                                                                 85
Technology                                                                                  68
Manufacturing                                                                               66
missing                                                                                     48
Other                                                                                       47
Hospitality                                                                                 42
Education                                                                                   41
Construction                             

In [248]:
industry_mapping = {
    'Retail': 'Retail',
    'Retail or Manufacturing': 'Retail',
    'Retail or Technology': 'Retail',
    'Retail (Automotive)': 'Retail',
    'Retail (Furniture)': 'Retail',
    'Retail (Beauty Industry)': 'Retail',
    'Retail or Healthcare': 'Retail',
    'Retail or Food Service': 'Retail',
    'Retail or Finance': 'Retail',
    'Retail, Technology': 'Retail',
    'Retail Banking, Real Estate, Insurance, Marketing': 'Retail',
    'Retail, Automotive': 'Retail',
    'Retail or Marketing Agency': 'Retail',
    'Retail or Telemarketing': 'Retail',
    'Retail, Beauty': 'Retail',
    'Retail, other (Transportation)': 'Retail',
    'Food and Beverage': 'Food & Beverage',
    'F&B Restaurant': 'Food & Beverage',
    'F&B (Restaurants Management)': 'Food & Beverage',
    'Food and Beverage, Beauty': 'Food & Beverage/Beauty',
    'Food and Beverage, Real Estate, Admin, other (Beauty Services)': 'Food & Beverage',
    'Food and Beverage or Retail': 'Food & Beverage',
    'Healthcare': 'Healthcare',
    'Fitness, Healthcare': 'Healthcare',
    'Hospitality': 'Hospitality',
    'Hospitality, Travel': 'Hospitality',
    'Hospitality or Food Industry': 'Hospitality',
    'Hospitality, Healthcare': 'Healthcare',
    'Technology': 'Technology',
    'IT': 'Technology',
    'Technology or Manufacturing': 'Technology',
    'Technology or other': 'Technology',
    'Technology or Business Services': 'Services',
    'Technology or IT': 'Technology',
    'Technology or Energy (Oil & Gas)': 'Energy',
    'Manufacturing': 'Manufacturing',
    'Manufacturing (Furniture)': 'Manufacturing',
    'Manufacturing (Packaging)': 'Manufacturing',
    'Manufacturing or Service industry (Technical and cleaning company)': 'Manufacturing',
    'Technology or Manufacturing/Services (Immigration)': 'Manufacturing',
    'Manufacturing/Utilities': 'Manufacturing',
    'Technology or other (as some elements of this job might be related to IT industry)': 'Technology',
    'Real Estate': 'Real Estate',
    'Real Estate or Construction': 'Construction',
    'Construction': 'Construction',
    'Construction (Interior decoration)': 'Construction',
    'Education': 'Education',
    'Education or Human Resources': 'Human Resources',
    'Banking': 'Banking',
    'Banking, Finance': 'Banking',
    'Financial Services': 'Finance',
    'Finance': 'Finance',
    'Advertising / Branding / Exhibition Design': 'Advertising',
    'Advertising & Marketing': 'Advertising/Marketing',
    'Advertising / Branding / Exhibition Design, Technology (assuming AdTech or Design Tech)': 'Advertising',
    'Marketing, Advertising': 'Advertising',
    'Marketing, Retail': 'Retail',
    'Advertising, Branding, Exhibition Design': 'Advertising',
    'Logistics': 'Logistics',
    'Logistics/Freight Forwarding': 'Logistics',
    'Logistics and Transportation': 'Logistics',
    'Service': 'Services',
    'Service Industry': 'Services',
    'Service Industry/Personal Services': 'Services',
    'Security': 'Security',
    'Event management, other': 'Services',
    'Recreation': 'Recreation',
    'Travel': 'Travel',
    'Tourism': 'Tourism',
    'Animal Services': 'Services',
    'Pharmaceuticals': 'Pharmaceuticals',
    'MEP Works': 'Services',
    'Energy': 'Energy',
    'Ecommerce': 'Ecommerce',
    'Luxury Hospitality': 'Hospitality',
    'Digital Technology': 'Technology',
    'Facilities Management': 'Management',
    'Corporate Finance': 'Finance',
    'Law': 'Law',
    'Telecommunications': 'Technology',
    'Media and Entertainment': 'Entertainment',
    'Agriculture': 'Agriculture',
    'Beauty/Cosmetics': 'Cosmetics',
    'Beauty and Personal Care': 'Cosmetics',
    'Beauty': 'Cosmetics',
    'Cleaning and Technical Services': 'Services',
    'Furniture/Retail': 'Retail',
    'Printing Service Company, Manufacturing': 'Services',
    'Interior Design': 'Recreation',
    'Retail or Telemarketing': 'Retail',
    'Retail or Travel and Tourism': 'Retail',
    'Real Estate or Construction': 'Construction'
}

new_df['Industry'] = new_df['Industry'].map(lambda x: industry_mapping.get(x, 'Other'))

new_df['Industry'].value_counts()

Industry
Other                     311
Retail                    130
Healthcare                 88
Real Estate                85
Technology                 79
Manufacturing              70
Hospitality                46
Construction               42
Education                  41
Food & Beverage            27
Finance                    17
Advertising                15
Services                   11
Travel                      6
Banking                     5
Logistics                   4
Tourism                     3
Cosmetics                   3
Energy                      2
Entertainment               2
Human Resources             2
Recreation                  2
Agriculture                 2
Pharmaceuticals             1
Ecommerce                   1
Food & Beverage/Beauty      1
Security                    1
Law                         1
Management                  1
Advertising/Marketing       1
Name: count, dtype: int64

In [249]:
new_df.isna().sum()

Experience                0
Job Type                  0
Location                  0
Education Level           0
Major                     0
Level                     0
Job Function              0
Industry                  0
Expected_Salary_in_USD    0
Salary_in_USD             0
dtype: int64

In [250]:
new_df.duplicated().sum()

22

In [251]:
# new_df = new_df.drop_duplicates()

In [252]:
new_df.duplicated().sum()

22

In [253]:
new_df.describe()

Experience  Expected_Salary_in_USD  Salary_in_USD
count  1000.00000            1.000000e+03    1000.000000
mean      1.81800            6.818926e+07    2290.354332
std       2.28738            2.154141e+09   19398.610667
min       0.00000            2.997275e+00      14.850136
25%       0.00000            8.174387e+02     681.198910
50%       1.00000            1.226158e+03     991.668413
75%       3.00000            3.746594e+04    1634.877384
max      30.00000            6.812000e+10  587500.000000

In [254]:
new_df.describe(include=['object'])

Job Type Location Education Level  Major    Level Job Function  \
count        1000     1000            1000   1000     1000         1000   
unique          7       11               8     10       13          299   
top     Full-time      UAE         Unknown  Other  Unknown        Sales   
freq          935      870             653    333      422          178   

       Industry  
count      1000  
unique       30  
top       Other  
freq        311

In [255]:
LLM_Expected_salary = new_df[['Expected_Salary_in_USD', 'Salary_in_USD']]
LLM_Expected_salary

Expected_Salary_in_USD  Salary_in_USD
0              1.236264e+03    1236.263736
1              1.117830e+04    3746.543040
2              1.510989e+05    1510.989011
3              1.236264e+03     686.813187
4              9.478022e+02     947.802198
5              1.098901e+05    1098.901099
6              8.241758e+02     824.175824
7              3.405995e+05    3405.994550
8              4.386921e+03     599.455041
9              4.087193e+01    2452.316076
10             8.175749e+02     817.574932
11             1.158038e+06   11580.381471
12             3.814714e+03    3814.713896
13             1.907357e+05    1907.356948
14             6.811989e+02     681.198910
15             6.130790e+02     613.079019
16             6.811989e+02     681.198910
17             1.226158e+03     681.198910
18             1.226158e+03    1634.877384
19             1.226158e+05    1226.158038
20             1.771117e+03    1771.117166
21             1.294278e+03    1294.277929
22             6.130790e+02     613.079019
23             1.498638e+05    1498.637602
24             1.634877e+05    1634.877384
25             9.536785e+02     953.678474
26             2.724796e+05    2724.795640
27             5.449591e+02     408.719346
28             8.174387e+02     817.438692
29             1.226158e+03    3269.754768
30             6.811989e+02     681.198910
31             1.021798e+03    1021.798365
32             8.855586e+02     885.558583
33             1.089918e+03    1089.918256
34             4.768392e+02     476.839237
35             2.997275e+03    2997.275204
36             1.362398e+03    1362.397820
37             1.498638e+03    1226.158038
38             1.771117e+03    1771.117166
39             2.997275e+05    2997.275204
40             8.174387e+02    1634.877384
41             2.724796e+03    2724.795640
42             8.174387e+02    1634.877384
43             2.724796e+02     544.959128
44             9.536785e+02     953.678474
45             1.226158e+03    2179.836512
46             1.634877e+03    1634.877384
47             1.226158e+03     817.438692
48             8.855586e+02     885.558583
49             1.089918e+03    1089.918256
50             7.493188e+02     749.318801
51             1.907357e+03    1907.356948
52             4.087193e+02     817.438692
53             5.585831e+04     558.583106
54             4.495913e+02     449.591281
55             1.089918e+03    1089.918256
56             6.811989e+02     681.198910
57             2.588556e+05    2588.555858
58             1.634877e+03    1634.877384
59             4.359673e+02     435.967302
60             1.226158e+03    1634.877384
61             1.226158e+03    1089.918256
62             4.768392e+02     476.839237
63             1.226158e+03     749.318801
64             6.130790e+02     613.079019
65             7.493188e+02     749.318801
66             1.226158e+03     817.438692
67             6.130790e+04     613.079019
68             6.811989e+02     681.198910
69             2.724796e+03    2724.795640
70             1.021798e+05    1021.798365
71             1.362398e+02     136.239782
72             2.316076e+05    2316.076294
73             4.087193e+02     817.438692
74             1.226158e+03     817.438692
75             9.536785e+02     953.678474
76             1.975477e+05    1975.476839
77             1.634877e+05    1634.877384
78             6.811989e+02     681.198910
79             3.405995e+05    3405.994550
80             8.174387e+02     817.438692
81             3.814714e+03    3814.713896
82             4.904632e+03    4904.632153
83             2.043597e+03    2043.596730
84             7.493188e+02     749.318801
85             5.177112e+02     517.711172
86             1.226158e+03    1226.158038
87             1.226158e+03    1226.158038
88             6.403270e+02     640.326975
89             3.405995e+05    3405.994550
90             1.226158e+03    1226.158038
91             1.226158e+03    1226.158038
92    

In [256]:
LLM_Expected_salary.to_csv("LLM_Expected_salary.csv", index=False)

## I will drop Job Function	and Expected salary in USD

In [259]:
new_df = new_df.drop(columns=['Job Function', 'Expected_Salary_in_USD'])

In [260]:
new_df.to_csv("processed_job_descriptions_for_ml.csv", index=False)